In [4]:
import numpy as np
import pandas as pd
import tensorflow as tf
from sklearn.preprocessing import MinMaxScaler
import yfinance as yf
from scipy.stats import gaussian_kde
import plotly.graph_objects as go

# Load the data
data = yf.download('AAPL', '2022-02-02', '2024-02-02')
data = data[['Close']]  # Use the 'Close' price for prediction
data['Date'] = pd.to_datetime(data.index)
data.set_index('Date', inplace=True)

# Normalize the data
scaler = MinMaxScaler(feature_range=(0, 1))
scaled_data = scaler.fit_transform(data)

# Create training and test datasets
train_size = int(len(scaled_data) * 0.8)
train_data = scaled_data[:train_size]
test_data = scaled_data[train_size:]

# Create sequences for training
def create_sequences(data, seq_length):
    X, y = [], []
    for i in range(len(data) - seq_length):
        X.append(data[i:i + seq_length])
        y.append(data[i + seq_length])
    return np.array(X), np.array(y)

seq_length = 60  # Use 60 days of data to predict the next day's price
X_train, y_train = create_sequences(train_data, seq_length)
X_test, y_test = create_sequences(test_data, seq_length)

# Create a neural network model using TensorFlow
model = tf.keras.Sequential([
    tf.keras.layers.LSTM(50, return_sequences=True, input_shape=(seq_length, 1)),
    tf.keras.layers.LSTM(50, return_sequences=False),
    tf.keras.layers.Dense(25),
    tf.keras.layers.Dense(1)
])

model.compile(optimizer='adam', loss='mean_squared_error')

# Train the model on the historical data
model.fit(X_train, y_train, batch_size=1, epochs=1)

# Get the last sequence from the training data
last_sequence = train_data[-seq_length:]

# Number of future days to predict
future_days = 300

# Generate multiple future predictions to create a distribution
num_simulations = 100
all_predictions = []

for _ in range(num_simulations):
    current_sequence = last_sequence
    future_predictions = []
    for _ in range(future_days):
        current_sequence_reshaped = current_sequence.reshape((1, seq_length, 1))
        next_value = model.predict(current_sequence_reshaped)
        future_predictions.append(next_value[0, 0])
        current_sequence = np.append(current_sequence[1:], next_value, axis=0)
    all_predictions.append(future_predictions)

all_predictions = np.array(all_predictions)
all_predictions = scaler.inverse_transform(all_predictions)

# Flatten the predictions to estimate the PDF
flattened_predictions = all_predictions.flatten()

# Estimate the PDF using Gaussian Kernel Density Estimation
kde = gaussian_kde(flattened_predictions)

# Create a grid of points for the 3D plot
x = np.linspace(min(flattened_predictions), max(flattened_predictions), 100)
y = np.linspace(1, future_days, future_days)
X, Y = np.meshgrid(x, y)

# Evaluate the PDF on the grid
Z = np.array([kde(x) for x in X])

# Create a 3D plot using Plotly
fig = go.Figure(data=[go.Surface(z=Z, x=X, y=Y, colorscale='Viridis')])

fig.update_layout(
    title='Probability Density of Future Stock Prices',
    scene=dict(
        xaxis_title='Stock Price',
        yaxis_title='Days into the Future',
        zaxis_title='Probability Density'
    )
)

fig.show()

[*********************100%%**********************]  1 of 1 completed
/var/folders/mk/fn7b709x3dz4m442ngj1_xf00000gn/T/ipykernel_62306/2297774977.py:12: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



1/1 [==============================] - 0s 22ms/step
